# 04_Geoviews_Datashader_NLDN

## Overview:
1. Read in a multi-million row dataframe containing National Lightning Detection Network data from August 2021
1. Use `Datashader` to create a rasterized representation of the dataframe
1. Create an interactive, georeferenced visualization of NLDN data using the [Holoviz](https://holoviz.org) ecosystem

## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| Pandas  | Necessary | |
| Geoviews 1-2  | Necessary| |

* **Time to learn**: 30 minutes
***

## Imports

In [ ]:
import datashader as ds
import pandas as pd
from colorcet import fire
from datashader import transfer_functions as tf
import geoviews as gv
from geoviews import opts
import holoviews as hv
from holoviews.element.tiles import OSM
from holoviews.operation.datashader import datashade,rasterize

In [ ]:
hv.extension('bokeh')

## Read in a multi-million row dataframe containing National Lightning Detection Network data from August 2021

Here, we load in all of the detected cloud-to-ground flashes from August 2021. The data was originally derived from a Pandas-friendly text file, with over 50 million lines (one per flash, cloud-to-cloud as well as cloud-to-ground). While we could use Pandas `read_csv` to create a `Dataframe` from it, here we read in the dataset as expressed in [Feather](https://arrow.apache.org/docs/python/feather.html) format.

In [ ]:
%time df = pd.read_feather('/spare11/atm533/data/202108_NLDN_CG.ftr')

<div class="alert alert-info">Typically, it takes less than 30 seconds to load in this Feather-formatted file, and requires a maximum of 10 GB of system memory (once loaded, about 2.7GB). Pretty signficant, but in comparison, loading the same dataset in ASCII format takes close to 10 minutes and 60 GB of RAM!

In [ ]:
df

<div class="alert alert-info"><b>Did you know?</b> The NLDN was originally developed in our department in the 1980s! It is now operated by Vaisala. </div>

## Plot flash locations using Pandas' Matplotlib Scatterplot interface.

In [ ]:
df.plot.scatter('Lon','Lat',figsize=(11,8));

The plot takes a while to appear, and is essentially useless due to the thousands upon thousands of overlapping points. It seems impossible to make a useful plot of a month's worth (tens of millions of flashes during the warm season) of lightning strikes ... until we leverage the `Datashader` library, which is part of `Holoviz`.

## Use `Datashader` to create a rasterized representation of the dataframe

First, we will directly use `Datashader` methods to produce a visualization. We set up a Datashader `Canvas` object of x by y pixels, and then *aggregate* each point into a raster image of the specified x by y dimensions.

Then, we use Datashader's `transfer_functions` methods to set a colormap and a background.

In [ ]:
agg = ds.Canvas(800,600).points(df,'Lon','Lat')
tf.set_background(tf.shade(agg, cmap=fire),"black")

What previously took a minute or so and provided only the coarsest amount of detail, now takes place in seconds and the detail is such that we can clearly see the implied geography!

However, as cool (or, in the case of this colormap, hot) as the above graphic is, it has no interactivity nor georeferencing (technically, a `Datashader` object has no concept of things like `axes` or `colorbar`s. 

Holoviews and Geoviews to the rescue!

## Create an interactive, georeferenced visualization of NLDN data using the [Holoviz](https://holoviz.org) ecosystem

First, create a Geoviews dataset from the Pandas dataframe

In [ ]:
gdf = gv.Dataset(df)

Now, we create two Geoviews objects; one for a background map, and the other, NLDN flash locations derived from GeoViews' representation of the underlying Dataframe. 

In [ ]:
map_tiles  = OSM().opts(alpha=0.9,width=900, height=700)
points     = gv.Points(gdf, ['Lon','Lat'])

## Rasterize (and datashade) the points.

In [ ]:
flashes = rasterize(points, x_sampling=.001, y_sampling=.001, cmap=fire, alpha=100)

<div class="alert alert-info"><b>Note: </b>
<ol>
<li>x_ and y_sampling specify to what resolution the points should be sampled from, using the distance coordinates relevant to the dataset. Here, we specify to sample every thousandth of a degree.</li>
    <li>We specify the <code>alpha</code> argument as a value from 0 to 255 here, as opposed to a floating point range of 0 to 1. This will make it so we can see the underlying map background.</li></ol></div>

## Add in some options
We'll add a colorbar, a log scale, and the hover tool.

In [ ]:
flashes = flashes.opts(colorbar=True,logz=True,width=900,height=700,tools=['hover'])

## Create the final graphic
Overlay the rasterized flashes with the OpenStreetMaps background

In [ ]:
flashmap = map_tiles * flashes

## View and interact with the map

In [ ]:
flashmap

<div class="alert alert-info"><b>TIP:</b> Turn off the hover tool before panning and zooming, and then turn it back on when you are at your desired level of zoom or pan location). </div>

Notice how quickly the map updates! The rasterized image's detail changes with zoom just as you are used to with other web-based mapping tools, such as Google Maps!

<div class="alert alert-warning"><b>Things to try:</b> 
Zoom in all the way so you can see the UAlbany uptown campus on the map. You will see cloud-to-ground lightning strikes very close to the ETEC building.
    
Examine the Pandas dataframe: subset latitude and longitude so you can determine when these strikes occurred.</div>

---
## Summary
* We have successfully and efficiently loaded, visualized, and interacted with a very large dataset!
* Nevertheless, the memory footprint remains large enough so that it is not practical to have several users working with this dataset simultaneously.

### What's Next?
Take a look at [hvPlot](https://hvplot.holoviz.org/), a higher-level interface to Holoviz packages such as Geoviews and Datashader.

### References:
1. [National Lightning Detection Network](https://www.vaisala.com/en/products/national-lightning-detection-network-nldn)
1. [Datashader](https://datashader.org/getting_started/Introduction.html)
1. [Large Data in Holoviews](http://holoviews.org/user_guide/Large_Data.html)